In [1]:
import numpy as np
from pathlib import Path

from pymor.basic import *
from pymor.core.pickle import load

from RBInvParam.problems.problems import build_InstationaryModelIP

set_log_levels({
    'pymor' : 'WARN'
})

set_defaults({})


In [2]:
WORK_DIR = Path('/home/benedikt/Dokumente/parabolische_inverse_probleme')
data_dir_path = WORK_DIR / Path('examples/reaction/dumps')

FOM_data_path = data_dir_path / Path('FOM_IRGNM.pkl')
QrROM_data_path = data_dir_path / Path('Qr_IRGNM.pkl')
#QrROM_data_path = None
QrVrROM_data_path = None

data = {}

if FOM_data_path:
    with open(FOM_data_path, 'rb') as file:
        FOM_data = load(file)
    data['FOM'] = FOM_data

    if 'FOM' not in globals():
        _, FOM = build_InstationaryModelIP(
        setup=FOM_data['setup']
    )

    FOM_q_final = FOM_data['optimizer_statistics']['q'][-1]

if QrROM_data_path:
    with open(QrROM_data_path, 'rb') as file:
        QrROM_data = load(file)
    data['QrROM'] = QrROM_data

    QrROM_q_final = QrROM_data['optimizer_statistics']['q'][-1]


if QrVrROM_data_path:
    with open(QrVrROM_data_path, 'rb') as file:
        QrVrROM_data = load(file)
    data['QrVrROM'] = QrVrROM_data
    
    QrVrROM_q_final = QrVrROM_data['optimizer_statistics']['q'][-1]

q_exact = FOM_data['setup']['model_parameter']['q_exact']


[2025-01-16 09:31:13,955][discretize_instationary_IP] - noise percentage is 1.9179e-08
[2025-01-16 09:31:13,955][discretize_instationary_IP] - noise_level is 1.0000e-08


In [3]:
print("Total runtime:")

times = {}

for name, d in data.items():
    times[name] = int(np.ceil(d['optimizer_statistics']['total_runtime']))

    if name == 'FOM':
        speed_up_str = ' | --'
    if name == 'QrROM':
        speed_up = times['FOM'] / times['QrROM'] 
        speed_up_str = f' | {speed_up:3.3}'
    if name == 'QrVrROM':
        speed_up = times['FOM'] / times['QrVrROM'] 
        speed_up_str = f' | {speed_up:3.3}'
    

    print(f"{name} : {times[name]}s" + speed_up_str)

Total runtime:
FOM : 1s | --
QrROM : 1s | 1.0


In [4]:
val = FOM_q_final
rel = q_exact

x = FOM.products['bochner_prod_Q'].apply2(rel-val, rel-val) 
y = FOM.products['bochner_prod_Q'].apply2(rel, rel) 
z = np.sqrt(x) / np.sqrt(y) * 100
print(f"{z:3.4e}")

6.1772e+01


In [5]:
val = QrROM_q_final
rel = FOM_q_final

x = FOM.products['bochner_prod_Q'].apply2(rel-val, rel-val) 
y = FOM.products['bochner_prod_Q'].apply2(rel, rel) 
z = np.sqrt(x) / np.sqrt(y) * 100
print(f"{z:3.4e}")

0.0000e+00


In [6]:
FOM.visualizer.visualize(q_exact)

In [7]:
FOM.visualizer.visualize(FOM_q_final)

In [8]:
FOM.visualizer.visualize(QrROM_q_final)